In [1]:
from sklearn import preprocessing as pp
import numpy as np
from music21 import converter, instrument, note, chord, stream
import glob
import pickle
from keras.utils import np_utils
from keras.models import Sequential
from keras.layers import Dense
from keras.layers import Dropout
from keras.layers import LSTM
from keras.layers import Activation
from keras.layers import BatchNormalization as BatchNorm
from keras.layers import Lambda
from keras.callbacks import ModelCheckpoint
from keras.models import load_model
from numpy.random import multinomial as randm

# Current Counts = Current Counts + Note Length % 16 ?

def buildNotes():
    
    print("In buildNotes()")
    
    notes = []
    noteLengths = []
    
    for file in glob.glob("Music/*.mid"):
        
        try:
            midi = converter.parse(file)    
            
        except:
            print("MIDI file %s failed to parse" % file)
            continue
            
        print("Parsing %s" % file)
        notesToParse = None
        
        try: # file has instrument parts
            s2 = instrument.partitionByInstrument(midi)
            notesToParse = s2.parts[0].recurse()
            print("Instrument Parts %d" % len(s2.parts))
            
        except: # file has notes in a flat structure
            notesToParse = midi.flat.notes
            
        # For each note in notesToParse (a stream of notes)
            
        for element in notesToParse:
            
            # Interesting parameters of notes that we may want to look at here.
            
            if isinstance(element, note.Note):
                notes.append(str(element.pitch))
                noteLengths.append(str(float(element.quarterLength)))
                
            elif isinstance(element, chord.Chord):
                notes.append('.'.join(str(n) for n in element.normalOrder))
                noteLengths.append(str(float(element.quarterLength)))

    pickle.dump(notes, open('notes.p', 'wb'))
    pickle.dump(noteLengths, open('noteLengths.p', 'wb'))

    return notes, noteLengths

def prepareSeq(notes, noteLengths):

    seqLength = 4 # S Sequence Length
    inputSize = len(notes) - seqLength # N Samples
    categories = 2 # C Categories
    
    # Yields N x S x C array
    
    pitchSet = sorted(set(notes))
    npitch = len(pitchSet)
    noteToInt = dict((note, number) for number, note in enumerate(pitchSet))
    
    lengthSet = sorted(set(noteLengths))
    nlengths = len(lengthSet)
    lengthToInt = dict((length, number) for number, length in enumerate(lengthSet))
    
    # We only have 2 dimensions at the moment, pitch and length
    # noteIn - a collection of categorical arrays, each row is one category
    # noteOut - the integer which converts to the index of that category's respective
    # one hot encoding.  These categorical one hot encodings are later concatenated
    # columnwise to form a multi hot encoding.

    # This representation is a C x N x S array
    
    noteIn = [
        [],
        []
    ]
    
    noteOut = [
        [],
        []
    ]

    # Mapping of i:i+seqLength notes to note i + seqLength
    
    # X[0] sequence_in : [seqLength]
    # X[1] length_in : [seqLength]
    
    # Y[0] sequence_out : 1
    # Y[1] length_out : 1
    
    for i in range(0, inputSize, 1):
        
        sequence_in = notes[i:i + seqLength]
        sequence_out = notes[i + seqLength]
        
        length_in = noteLengths[i:i + seqLength]
        length_out = noteLengths[i + seqLength]
        
        noteIn[0].append([noteToInt[char] for char in sequence_in])
        noteIn[1].append([lengthToInt[char] for char in length_in])
        
        noteOut[0].append(noteToInt[sequence_out])
        noteOut[1].append(lengthToInt[length_out])
        
    # npatterns = len(noteIn) (inputSize)

    # reshape the input into a format compatible with LSTM layers
    # noteIn = np.reshape(noteIn, (inputSize, seqLength, 1))
    
    noteIn = np.array(noteIn, dtype=float)
    noteOut = np.array(noteOut, dtype=float)
    
    # normalize input
    noteIn[0] = noteIn[0] / float(npitch)
    noteIn[1] = noteIn[1] / float(nlengths)
    
    print("noteIn shape:")
    print(noteIn.shape)
    print("noteOut shape:")
    print(noteOut.shape)
    print(noteIn)
    
    catNote = np_utils.to_categorical(noteOut[0])
    catLength = np_utils.to_categorical(noteOut[1])
    
    # Concatenate the input arrays row wise
    # Concatenate the categorical arrays along axis 1 (columnwise)
    
    print("noteIn:")
    print(noteIn)
    
    # Convert from C x N x S to N x S x C
    
    reshape = []
    for N in range(inputSize):
        for S in range(seqLength):
            for C in range(categories):
                reshape.append(noteIn[C][N][S])
    
    dout = np.concatenate((catNote, catLength), 1)
    din = np.reshape(reshape, (inputSize, seqLength, categories))
    
    print("din shape:")
    print(din.shape)
    print("dout shape:")
    print(dout.shape)
    print("din:")
    print(din)
    
    print(len(catNote[0]))
    print(len(catLength[0]))
    
    print(din[0][0][0])
    print(din[0][0][1])

    return (din, dout)


Using TensorFlow backend.
C:\Users\root\anaconda3\lib\site-packages\tensorflow\python\framework\dtypes.py:516: FutureWarning: Passing (type, 1) or '1type' as a synonym of type is deprecated; in a future version of numpy, it will be understood as (type, (1,)) / '(1,)type'.
  _np_qint8 = np.dtype([("qint8", np.int8, 1)])
C:\Users\root\anaconda3\lib\site-packages\tensorflow\python\framework\dtypes.py:517: FutureWarning: Passing (type, 1) or '1type' as a synonym of type is deprecated; in a future version of numpy, it will be understood as (type, (1,)) / '(1,)type'.
  _np_quint8 = np.dtype([("quint8", np.uint8, 1)])
C:\Users\root\anaconda3\lib\site-packages\tensorflow\python\framework\dtypes.py:518: FutureWarning: Passing (type, 1) or '1type' as a synonym of type is deprecated; in a future version of numpy, it will be understood as (type, (1,)) / '(1,)type'.
  _np_qint16 = np.dtype([("qint16", np.int16, 1)])
C:\Users\root\anaconda3\lib\site-packages\tensorflow\python\framework\dtypes.py:519

In [2]:
# print(np.arange(10).reshape(5,2).T.flatten())
notes, noteLengths = buildNotes()
noteIn, noteOut = prepareSeq(notes, noteLengths)
print(noteIn.shape)
print(noteOut.shape)

In buildNotes()
Parsing Music\Fugue1.mid
Parsing Music\Fugue10.mid
Parsing Music\Fugue11.mid
MIDI file Music\Fugue12.mid failed to parse
Parsing Music\Fugue13.mid
Parsing Music\Fugue14.mid
Parsing Music\Fugue15.mid
Parsing Music\Fugue16.mid
Parsing Music\Fugue17.mid
Parsing Music\Fugue18.mid
MIDI file Music\Fugue19.mid failed to parse
Parsing Music\Fugue2.mid
Parsing Music\Fugue20.mid
Parsing Music\Fugue21.mid
Parsing Music\Fugue22.mid
Parsing Music\Fugue23.mid
Parsing Music\Fugue24.mid
Parsing Music\Fugue3.mid
Parsing Music\Fugue4.mid
Parsing Music\Fugue5.mid
MIDI file Music\Fugue6.mid failed to parse
Parsing Music\Fugue7.mid
Parsing Music\Fugue8.mid
Parsing Music\Fugue9.mid
Instrument Parts 1
noteIn shape:
(2, 22374, 4)
noteOut shape:
(2, 22374)
[[[0.60759494 0.67088608 0.7721519  0.87341772]
  [0.67088608 0.7721519  0.87341772 0.97468354]
  [0.7721519  0.87341772 0.97468354 0.87341772]
  ...
  [0.56962025 0.50632911 0.48101266 0.40506329]
  [0.50632911 0.48101266 0.40506329 0.784810

In [3]:
def createNet(noteIn, nvocab):

    print("In createNet()")
    
    print(noteIn.shape)
    
    model = Sequential()
    model.add(LSTM(
        512,
        input_shape=(noteIn.shape[1], noteIn.shape[2]),
        recurrent_dropout=0.3,
        return_sequences=True
    ))
    
    # Chris's code
    model.add(LSTM(
        512,
        input_shape=(noteIn.shape[1], noteIn.shape[2]),
        recurrent_dropout=0.3,
        return_sequences=False
    ))
    
    model.add(BatchNorm())
    model.add(Dropout(0.3))
    model.add(Dense(256))
    model.add(Activation(activation='relu'))
    model.add(BatchNorm())
    model.add(Dropout(0.3))
    
    #model.add(Flatten())
    
    model.add(Dense(nvocab))
    model.add(Lambda(lambda x: x / 0.6))
    model.add(Activation(activation='softmax'))

    model.compile(
            loss='categorical_crossentropy',
            optimizer='adam',
            metrics=['accuracy']
        )
    
    return model

def trainNet(_epochs=1):
    """ Train a Neural Network to generate music """
    notes, noteLengths = buildNotes()

    nvocab = len(set(notes)) + len(set(noteLengths))
    
    noteIn, noteOut = prepareSeq(notes, noteLengths)
    
    model = createNet(noteIn, nvocab)
 
    checkpoint = ModelCheckpoint(
        "weights2-improvement-{epoch:02d}-{loss:.4f}-bigger.hdf5",
        monitor='loss',
        verbose=0,
        save_best_only=True,
        mode='min'
    )

    callbacks_list = [checkpoint]

    # Your line of code here
    model.fit(noteIn, noteOut, batch_size=1024, epochs=_epochs, verbose=1, callbacks=callbacks_list)
    


In [24]:
trainNet(100)

In buildNotes()
Parsing Music\Fugue1.mid
Parsing Music\Fugue10.mid
Parsing Music\Fugue11.mid
MIDI file Music\Fugue12.mid failed to parse
Parsing Music\Fugue13.mid
Parsing Music\Fugue14.mid
Parsing Music\Fugue15.mid
Parsing Music\Fugue16.mid
Parsing Music\Fugue17.mid
Parsing Music\Fugue18.mid
MIDI file Music\Fugue19.mid failed to parse
Parsing Music\Fugue2.mid
Parsing Music\Fugue20.mid
Parsing Music\Fugue21.mid
Parsing Music\Fugue22.mid
Parsing Music\Fugue23.mid
Parsing Music\Fugue24.mid
Parsing Music\Fugue3.mid
Parsing Music\Fugue4.mid
Parsing Music\Fugue5.mid
MIDI file Music\Fugue6.mid failed to parse
Parsing Music\Fugue7.mid
Parsing Music\Fugue8.mid
Parsing Music\Fugue9.mid
Instrument Parts 1
noteIn shape:
(2, 22374, 4)
noteOut shape:
(2, 22374)
[[[0.60759494 0.67088608 0.7721519  0.87341772]
  [0.67088608 0.7721519  0.87341772 0.97468354]
  [0.7721519  0.87341772 0.97468354 0.87341772]
  ...
  [0.56962025 0.50632911 0.48101266 0.40506329]
  [0.50632911 0.48101266 0.40506329 0.784810

In [20]:
def generate(model):
    
    print("In Generate")
    
    notes = pickle.load(open('notes.p', 'rb'))
    noteLengths = pickle.load(open('noteLengths.p', 'rb'))

    pitchSet = sorted(set(notes))
    lengthSet = sorted(set(noteLengths))
    
    # 1. Call to prepareSeqPred
    
    noteIn = prepareSeqPred(notes, noteLengths) 
    
    # print("Model Loaded")
    
    # 2. Call to genNotes
    
    predOut = genNotes(model, noteIn, pitchSet, lengthSet)
    
    # 3. Call to createMidi
    createMidi(predOut)

# 1.
    
def prepareSeqPred(notes, noteLengths):
    
    print("In Prepare Sequences Prediction")
    
    seqLength = 4
    inputSize = len(notes) - seqLength
    categories = 2
    
    pitchSet = sorted(set(notes))
    npitch = len(pitchSet)
    noteToInt = dict((note, number) for number, note in enumerate(pitchSet))
    
    lengthSet = sorted(set(noteLengths))
    nlengths = len(lengthSet)
    lengthToInt = dict((length, number) for number, length in enumerate(lengthSet))
    
    noteIn = [
        [],
        []
    ]
    
    noteOut = [
        [],
        []
    ]
    
    for i in range(0, inputSize, 1):
        
        sequence_in = notes[i:i + seqLength]
        length_in = noteLengths[i:i + seqLength]
        
        sequence_out = notes[i + seqLength]
        length_out = noteLengths[i + seqLength]
        
        noteIn[0].append([noteToInt[char] for char in sequence_in])
        noteOut[0].append(noteToInt[sequence_out])
        
        noteIn[1].append([lengthToInt[char] for char in length_in])
        noteOut[1].append(lengthToInt[length_out])
        
    noteIn = np.array(noteIn, dtype=float)
    noteOut = np.array(noteOut, dtype=float)
    
    # normalize input
    noteIn[0] = noteIn[0] / float(npitch)
    noteIn[1] = noteIn[1] / float(nlengths)
        
    reshape = []
    for N in range(inputSize):
        for S in range(seqLength):
            for C in range(categories):
                reshape.append(noteIn[C][N][S])
    
    din = np.reshape(reshape, (inputSize, seqLength, categories))
        
    print("din shape:")
    print(din.shape)
    print("din:")
    print(din)

    return din

# 2.

def genNotes(model, noteIn, pitchSet, lengthSet):
    
    """ Generate notes from the neural network based on a sequence of notes """
    # Starts the melody by picking a random sequence from the input as a starting point
    
    inputSize = len(noteIn)
        
    start = np.random.randint(0, inputSize - 1)
    pattern = noteIn[start] # Remember that it is an N x S x C
    
    print("pattern %s" % pattern)
        
    seqLength = len(pattern)
    categories = 2
    
    print("seqLength: %d" % seqLength)

    npitches = len(pitchSet)
    nlengths = len(lengthSet)
    
    print("npitches %d nlengths %d" % (npitches, nlengths))
    
    # TODO
    intToNote = dict((number, note) for number, note in enumerate(pitchSet))
    intToLength = dict((number, length) for number, length in enumerate(lengthSet))
    
    predOut = []
    
    print("In genNotes(): noteIn[start] = %s" % pattern)
    print("inputSize: %d" % inputSize)
    print("categories: %d" % categories)
    
    print("pitchSet %s" % pitchSet)
    print("lengthSet %s" % lengthSet)

    for i in range(1000):
        
        # Reshape a single sample into 1 x S x C array
        
        prediction_input = np.reshape(pattern, (1, seqLength, categories))
        
        print("prediction_input:")
        print(prediction_input)
        
        ### Complete the line below
        prediction = model.predict(np.array(prediction_input))
        print(len(prediction[0]))       
        print("prediction: %s" % prediction[0])
        print("prediction length: %d" % len(prediction[0]))
        
        predPitch = prediction[0][:npitches].astype('float64')
        predLength = prediction[0][npitches:].astype('float64')
        
        print("Before")
        print(predPitch)
        print(predLength)
        
        #predPitch /= sumNote
        #predLength /= sumLength
        
        print("sumNote %f sumLength %f" % (predPitch.sum(), predLength.sum()))
        
        predPitch /= predPitch.sum()
        predLength /= predLength.sum()
        
        print("After")
        print(predPitch)
        print(predLength)
        
        print("sumNote %f sumLength %f" % (predPitch.sum(), predLength.sum()))
        
        array = randm(1, predPitch)
        print("array predPitch: %s" % array)
        indexPitch = np.argmax(array)
        
        array = randm(1, predLength)
        print("array predLength: %s" % array)
        indexLength = np.argmax(array)
        
        #TODO return tuple pitch, length
        result = np.array([intToNote[indexPitch], intToLength[indexLength]])
        predOut.append(result)
        
        print("result %s" % result)
        
        append = np.reshape(np.array([indexPitch/float(npitches), indexLength/float(nlengths)]), (1,2))
        pattern = np.concatenate((pattern, append))
        
        print("pattern: %s" % pattern)
        
        pattern = pattern[1:len(pattern)]
        
    print(predOut)

    return predOut

# 3.
    
def createMidi(predOut):
    
    print("In createMidi()")
    
    tempo = 0.2
    
    offset = 0
    output_notes = []
    for pattern in predOut:
        if ('.' in pattern[0]) or pattern[0].isdigit():
            notes_in_chord = pattern[0].split('.')
            notes = []
            for current_note in notes_in_chord:
                new_note = note.Note(int(current_note))
                new_note.storedInstrument = instrument.Piano()
                if pattern[1] != '0.0':
                    new_note.quarterLength = float(pattern[1]) # Assign duration
                notes.append(new_note)
            new_chord = chord.Chord(notes)
            new_chord.offset = offset
            output_notes.append(new_chord)
        else:
            new_note = note.Note(pattern[0])
            new_note.offset = offset
            new_note.storedInstrument = instrument.Piano()
            if pattern[1] != '0.0':
                new_note.quarterLength = float(pattern[1]) # Assign duration
            output_notes.append(new_note)
        offset += tempo
    midi_stream = stream.Stream(output_notes)
    midi_stream.write('midi', fp='test_output.mid')


In [5]:
model = 0

In [23]:
# Load a previous model (dependency)
if model == 0:
    model = load_model("weights2-improvement-100-6.2245-bigger.hdf5")
generate(model)

In Generate
In Prepare Sequences Prediction
din shape:
(22374, 4, 2)
din:
[[[0.60759494 0.08571429]
  [0.67088608 0.08571429]
  [0.7721519  0.08571429]
  [0.87341772 0.14285714]]

 [[0.67088608 0.08571429]
  [0.7721519  0.08571429]
  [0.87341772 0.14285714]
  [0.97468354 0.        ]]

 [[0.7721519  0.08571429]
  [0.87341772 0.14285714]
  [0.97468354 0.        ]
  [0.87341772 0.        ]]

 ...

 [[0.56962025 0.02857143]
  [0.50632911 0.02857143]
  [0.48101266 0.08571429]
  [0.40506329 0.02857143]]

 [[0.50632911 0.02857143]
  [0.48101266 0.08571429]
  [0.40506329 0.02857143]
  [0.78481013 0.65714286]]

 [[0.48101266 0.08571429]
  [0.40506329 0.02857143]
  [0.78481013 0.65714286]
  [0.92405063 0.65714286]]]
pattern [[0.56962025 0.02857143]
 [0.6835443  0.17142857]
 [0.37974684 0.02857143]
 [0.48101266 0.08571429]]
seqLength: 4
npitches 79 nlengths 35
In genNotes(): noteIn[start] = [[0.56962025 0.02857143]
 [0.6835443  0.17142857]
 [0.37974684 0.02857143]
 [0.48101266 0.08571429]]
inputS

114
prediction: [6.74703508e-04 1.33819925e-03 5.32597490e-03 8.58967251e-05
 2.40473053e-03 5.16133907e-04 3.26078990e-03 4.20233409e-04
 1.01616699e-03 4.76975169e-04 3.20808613e-03 3.20458610e-04
 3.24043649e-04 3.12201009e-04 2.84453738e-04 6.67568063e-03
 2.97151692e-03 1.00331451e-03 1.55070549e-04 3.24950414e-03
 4.28821048e-04 1.56800880e-03 3.49556212e-04 9.57326964e-04
 2.49410677e-03 1.73262251e-03 4.05128021e-03 1.05304352e-03
 4.98682959e-03 5.54162718e-04 1.21792359e-02 3.70021840e-03
 7.43474113e-04 7.93168001e-05 1.93000189e-04 6.93511756e-05
 1.33552501e-04 2.19840353e-04 1.03404082e-03 7.02104066e-04
 3.44203645e-03 2.35563726e-04 5.60445897e-03 3.03387333e-06
 5.72732242e-04 6.74154508e-05 1.58824946e-03 9.22277613e-05
 7.13892048e-04 3.09983641e-03 2.45067029e-04 2.12137727e-03
 1.66067854e-03 2.44893669e-03 2.97997370e-02 6.84879662e-04
 4.81174327e-04 1.05146300e-05 2.37475702e-04 1.35359133e-03
 1.56795777e-05 2.32450591e-04 5.91269229e-04 1.10420980e-03
 9.27210

114
prediction: [6.6450625e-03 2.5481097e-03 1.6052851e-02 2.0782938e-04 7.6361503e-03
 3.1256455e-03 5.3317947e-03 1.1719589e-03 4.0498683e-03 3.4216552e-03
 8.2344525e-03 2.2446045e-03 5.0176884e-04 1.1189919e-03 1.0448779e-03
 1.2208685e-02 4.8462055e-03 2.6850633e-03 1.5876864e-03 8.4880535e-03
 2.0653491e-03 4.2531826e-03 5.9407479e-03 2.1669469e-03 7.3034959e-03
 4.3167239e-03 2.2030186e-02 5.0774431e-03 3.0310457e-03 2.4084374e-03
 2.6922947e-02 2.4707103e-02 2.8609482e-03 6.1087916e-04 2.2851294e-03
 6.1657140e-04 4.0201829e-03 8.5914804e-04 5.4828255e-03 4.0725861e-03
 9.5151728e-03 1.7899643e-03 1.1321244e-02 6.3879983e-05 3.6573107e-03
 1.1987217e-03 2.1107565e-03 1.5955665e-03 1.7355797e-03 9.2928531e-03
 7.2705629e-04 5.5085248e-03 6.2094787e-03 5.0130370e-03 1.6161792e-02
 3.1848275e-03 3.2238399e-03 2.1312710e-04 1.4179980e-03 3.8205902e-03
 6.7969388e-04 8.1042957e-04 1.5651666e-03 6.4650374e-03 1.4876670e-03
 2.6307737e-02 1.6801013e-03 2.0572608e-03 6.4339576e-04 8.75

114
prediction: [7.49245100e-03 2.55142548e-03 1.44025066e-03 8.86406458e-04
 2.87800413e-02 1.69382140e-03 4.71637351e-03 1.38683739e-04
 1.93563188e-04 2.66844244e-03 9.30940965e-04 5.39599478e-06
 1.20748364e-05 2.61236419e-05 1.71644473e-03 2.09137495e-03
 8.51711316e-04 5.62641653e-04 2.61428067e-05 3.77777760e-04
 2.32652485e-01 3.70907801e-05 1.18262554e-03 1.09482894e-03
 2.47630365e-02 6.91958761e-04 4.32910444e-03 4.91878927e-05
 1.09653898e-04 7.46837395e-05 5.81541030e-07 4.46381886e-03
 4.05690592e-08 2.75791332e-04 4.03237995e-04 1.95676534e-04
 2.06598652e-05 1.92035145e-06 5.04386798e-03 3.15027748e-04
 6.17750914e-07 2.08622034e-04 2.46819167e-04 1.19609088e-02
 3.43695465e-05 7.20879121e-04 1.07918095e-05 6.16635589e-05
 3.26959016e-05 3.90524804e-08 2.96947488e-04 7.26781436e-05
 4.10410546e-04 4.56994016e-08 1.46944913e-07 8.98003691e-06
 9.52032919e-04 2.01394828e-03 9.77323297e-03 1.80003326e-06
 3.66700561e-07 7.61177216e-04 6.54931937e-05 1.81952608e-04
 6.32116

114
prediction: [1.13947326e-02 3.38767469e-03 1.86663948e-03 1.19273725e-03
 6.73943534e-02 3.37800593e-03 7.05658598e-03 3.61748098e-04
 6.46815170e-04 3.89181706e-03 1.76763849e-03 2.03451200e-05
 3.98248449e-05 8.34460152e-05 3.71114630e-03 3.09148501e-03
 1.79548142e-03 8.37758533e-04 5.28623459e-05 1.14532374e-03
 1.57387286e-01 1.06355008e-04 2.12635100e-03 1.92082580e-03
 3.93678993e-02 1.63814041e-03 8.59077182e-03 1.41626733e-04
 1.59103452e-04 2.26422184e-04 3.95333018e-06 8.16759001e-03
 2.02405573e-07 5.98076440e-04 1.34703307e-03 3.61177779e-04
 4.07328516e-05 9.46892396e-06 8.84949788e-03 8.27257230e-04
 4.47468437e-06 3.32601689e-04 4.47652012e-04 1.63789522e-02
 1.47757644e-04 1.38499623e-03 3.31795236e-05 1.39711134e-04
 6.72715396e-05 4.06322044e-07 4.61423973e-04 1.90458770e-04
 7.46494159e-04 3.20820817e-07 4.53482158e-07 3.15561556e-05
 2.45368411e-03 3.48739815e-03 1.50766633e-02 7.54663552e-06
 1.51956988e-06 1.03256968e-03 1.29384862e-04 3.29483650e-04
 1.15247

...

 7.91638932e-09 1.88378202e-09 2.08037378e-07]
[6.03838438e-11 2.96436330e-31 4.11308574e-04 1.53397662e-06
 1.50874703e-05 5.10598766e-05 9.17816609e-02 1.15475690e-04
 1.47468207e-04 5.45877592e-05 3.04557383e-03 9.44389845e-04
 1.92751817e-04 1.97917200e-03 4.01836132e-06 2.05400959e-02
 7.84490185e-05 2.01536110e-04 3.07621993e-03 4.58355853e-03
 4.67157513e-01 1.18726948e-02 1.37742411e-03 4.83868970e-03
 4.65422776e-03 1.42430905e-02 2.09157402e-03 1.55468981e-04
 3.61369876e-03 6.46591885e-04 5.57129225e-03 1.83374609e-03
 1.33567999e-04 5.87037357e-05 5.40653884e-04]
sumNote 0.353987 sumLength 0.646013
After
[1.65564924e-01 2.82262457e-03 3.18596612e-03 4.98567924e-03
 7.79926729e-02 8.73261208e-04 1.03659909e-02 2.85242479e-04
 6.30876407e-04 6.98440388e-03 4.07545131e-03 1.79960225e-04
 1.64203547e-04 1.47729022e-03 1.14482842e-02 1.16593231e-02
 7.64119106e-04 8.23023904e-04 1.30651318e-04 4.54053197e-03
 1.67399095e-01 9.04602217e-04 1.29582868e-02 1.72934255e-02
 1.5235364

114
prediction: [4.15539145e-02 1.42123783e-03 2.16336362e-03 2.74860417e-03
 4.08539847e-02 7.23837526e-04 5.40309632e-03 1.74808723e-04
 2.94528581e-04 2.65471917e-03 1.99445733e-03 3.82300314e-05
 5.45974217e-05 3.24138760e-04 3.81550938e-03 3.71114630e-03
 6.30378840e-04 4.34207090e-04 5.90171076e-05 1.00380427e-03
 1.14795215e-01 2.37009677e-04 4.53649694e-03 4.03936952e-03
 5.18094115e-02 1.07796521e-04 2.83258082e-03 4.53471032e-04
 1.65413352e-04 2.47856689e-04 5.67137522e-06 8.25767592e-03
 2.14118344e-07 1.35074253e-03 1.95999281e-03 8.51680059e-04
 3.48795060e-04 5.67361749e-05 8.12926050e-03 2.61442794e-04
 9.81634116e-07 1.08276436e-04 1.83874479e-04 1.20256450e-02
 3.62904684e-04 8.03480099e-04 1.60668118e-04 1.30518645e-04
 3.47488094e-05 1.97591703e-07 2.19804875e-04 1.18590753e-04
 3.96413583e-04 1.55226445e-07 1.30154135e-07 1.49704520e-05
 8.50612670e-03 6.70822710e-03 2.79197339e-02 1.21903731e-05
 2.06900722e-06 5.00333903e-04 2.45847652e-04 1.44247478e-03
 4.86220

array predPitch: [0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 1 0 0 0 0 0 0 0 0 0 0 0 0
 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0
 0 0 0 0 0]
array predLength: [0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 1 0 0 0 0 0 0 0 0 0 0 0 0 0 0]
result ['8.11.2' '3.0']
pattern: [[0.81012658 0.57142857]
 [0.02531646 0.57142857]
 [0.92405063 0.17142857]
 [0.07594937 0.57142857]
 [0.30379747 0.57142857]]
prediction_input:
[[[0.02531646 0.57142857]
  [0.92405063 0.17142857]
  [0.07594937 0.57142857]
  [0.30379747 0.57142857]]]
114
prediction: [2.7530873e-02 3.9159739e-03 3.9781197e-03 2.7875770e-03 6.8121664e-02
 3.6315930e-03 9.9327443e-03 4.6130142e-04 7.0687500e-04 5.6458167e-03
 3.2620828e-03 7.1800423e-05 1.5661349e-04 2.8816867e-04 6.7044436e-03
 6.3244859e-03 2.5769083e-03 1.4306296e-03 1.2399265e-04 3.0027824e-03
 1.3457671e-01 4.2466106e-04 5.5698710e-03 3.9821621e-03 8.4696680e-02
 1.4061723e-03 1.0709711e-02 3.7792241e-04 3.0244951e-04 5.8815820e-04
 2.227

114
prediction: [2.4660464e-02 3.4428993e-03 4.7276299e-03 2.5611112e-03 3.7106071e-02
 2.9011911e-03 8.9933220e-03 2.6815780e-04 3.0993557e-04 5.3181555e-03
 2.4750619e-03 4.7700352e-05 1.0766338e-04 1.6502160e-04 4.7645522e-03
 7.2092116e-03 2.0397219e-03 1.3889819e-03 1.1027726e-04 2.4414172e-03
 2.1184273e-01 3.4124972e-04 5.8005559e-03 3.5537458e-03 8.9279070e-02
 1.0563119e-03 8.9803208e-03 2.3866171e-04 2.9260261e-04 4.2283491e-04
 8.9944924e-06 9.2685102e-03 7.5140576e-07 1.5175906e-03 2.0709087e-03
 6.9419394e-04 3.2229829e-04 1.8067221e-05 9.5261242e-03 6.9720211e-04
 8.6123428e-06 3.5151179e-04 6.1291794e-04 5.7744114e-03 2.5877336e-04
 1.6183234e-03 6.6273336e-05 4.5714213e-04 1.4691068e-04 4.8869060e-06
 4.4849538e-04 6.3151494e-04 1.3599651e-03 1.8286372e-06 5.1691827e-06
 7.2008144e-05 2.8456005e-03 4.9052634e-03 2.1215752e-02 1.8421721e-05
 4.2463034e-06 9.4243855e-04 4.0727481e-04 9.5093052e-04 1.7615872e-02
 2.5349695e-03 1.5771216e-03 6.8710979e-05 4.6986362e-04 8.91

PermissionError: [Errno 13] Permission denied: 'test_output.mid'

In [120]:
generate(model)

In Generate
In Prepare Sequences Prediction
din shape:
(736, 4, 2)
din:
[[[0.46511628 0.2       ]
  [0.55813953 0.2       ]
  [0.65116279 0.2       ]
  [0.81395349 0.33333333]]

 [[0.55813953 0.2       ]
  [0.65116279 0.2       ]
  [0.81395349 0.33333333]
  [0.95348837 0.        ]]

 [[0.65116279 0.2       ]
  [0.81395349 0.33333333]
  [0.95348837 0.        ]
  [0.81395349 0.        ]]

 ...

 [[0.97674419 0.06666667]
  [0.1627907  0.26666667]
  [0.8372093  0.06666667]
  [0.58139535 0.2       ]]

 [[0.1627907  0.26666667]
  [0.8372093  0.06666667]
  [0.58139535 0.2       ]
  [0.34883721 0.06666667]]

 [[0.8372093  0.06666667]
  [0.58139535 0.2       ]
  [0.34883721 0.06666667]
  [0.51162791 0.8       ]]]
pattern [[0.81395349 0.2       ]
 [0.93023256 0.2       ]
 [0.3255814  0.06666667]
 [0.48837209 0.06666667]]
seqLength: 4
npitches 43 nlengths 15
In genNotes(): noteIn[start] = [[0.81395349 0.2       ]
 [0.93023256 0.2       ]
 [0.3255814  0.06666667]
 [0.48837209 0.06666667]]
inputSiz

array predPitch: [0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 1 0 0 0 0 0 0 0 0
 0 0 0 0 0 0]
array predLength: [0 1 0 0 0 0 0 0 0 0 0 0 0 0 0]
result ['E4' '0.25']
pattern: [[0.46511628 0.06666667]
 [0.1627907  0.06666667]
 [0.65116279 0.06666667]
 [0.65116279 0.06666667]
 [0.65116279 0.06666667]]
prediction_input:
[[[0.1627907  0.06666667]
  [0.65116279 0.06666667]
  [0.65116279 0.06666667]
  [0.65116279 0.06666667]]]
58
prediction: [1.3251936e-03 2.1538190e-03 5.1055933e-05 1.7906200e-04 8.8226428e-04
 3.4546161e-03 2.6842657e-02 4.5336869e-02 8.1832928e-05 1.9438720e-04
 1.3683978e-03 1.6145708e-06 5.1306945e-04 4.6745094e-04 1.6554907e-03
 7.6005897e-05 1.3865913e-04 9.5951307e-04 6.2552508e-04 3.2841126e-04
 1.5616295e-02 4.3502485e-05 9.5697294e-05 1.4534686e-03 1.5431615e-03
 3.8331104e-03 9.5899159e-06 1.7825412e-02 8.5581884e-02 8.0381846e-03
 2.2820859e-04 9.5483717e-03 3.1843994e-04 2.0952216e-04 5.6019928e-02
 4.0731090e-04 1.2289716e-03 1.1946738e-03 3.3633431

 2.6869481e-02 2.1784890e-03 2.8165770e-04]
prediction length: 58
Before
[6.21047278e-04 7.19270683e-05 4.09530713e-07 4.76518726e-05
 4.86126228e-05 3.67396278e-03 5.27618174e-03 8.64670515e-01
 6.31222383e-06 7.36781067e-06 1.78260671e-05 1.31682043e-09
 2.11113971e-07 1.16863892e-04 2.64729606e-05 8.64072717e-07
 1.73527076e-06 8.61212320e-05 8.49237767e-05 1.38652496e-07
 8.32182064e-04 3.03838902e-07 1.92331368e-06 1.57358823e-04
 2.11617822e-04 2.23461047e-05 3.36125623e-07 1.92187377e-03
 6.36028275e-02 9.87121166e-05 4.40869781e-06 2.45235744e-04
 3.34939102e-07 7.75293574e-06 1.24841193e-02 1.89148250e-05
 1.25318256e-05 8.14203406e-04 6.16370244e-08 4.18558957e-05
 1.34914008e-05 4.25526341e-05 4.51737928e-04]
[2.30394676e-03 1.06348572e-02 4.53014945e-04 1.13551207e-04
 1.19800898e-04 8.43021510e-08 1.09362236e-06 1.93097425e-04
 8.00864364e-04 1.93490692e-07 1.65950773e-08 3.03686102e-04
 2.68694814e-02 2.17848900e-03 2.81657703e-04]
sumNote 0.955746 sumLength 0.044254
Afte

array predPitch: [0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 1 0 0
 0 0 0 0 0 0]
array predLength: [0 1 0 0 0 0 0 0 0 0 0 0 0 0 0]
result ['F3' '0.25']
pattern: [[0.65116279 0.06666667]
 [0.65116279 0.06666667]
 [0.72093023 0.86666667]
 [0.65116279 0.        ]
 [0.79069767 0.06666667]]
prediction_input:
[[[0.65116279 0.06666667]
  [0.72093023 0.86666667]
  [0.65116279 0.        ]
  [0.79069767 0.06666667]]]
58
prediction: [3.6506806e-04 2.7107078e-05 1.8324984e-06 1.7587899e-05 2.3528544e-05
 6.2302956e-03 9.1964200e-02 2.7922392e-03 4.2759082e-05 6.1904120e-06
 3.2614867e-04 7.7278196e-07 2.5377469e-05 2.1630526e-03 1.7213186e-03
 1.5879086e-05 4.1075559e-06 2.0574410e-03 3.7283417e-06 6.2127714e-05
 6.3954657e-03 5.4133643e-04 2.1485428e-05 3.5166193e-03 4.6285498e-03
 4.9684162e-04 4.9681526e-06 9.8909962e-04 4.4865049e-02 2.5315583e-02
 4.2705311e-04 1.4786702e-03 7.3393035e-06 8.1131649e-05 8.4084898e-02
 1.2719557e-03 5.5640354e-04 5.9832650e-04 1.6856251

58
prediction: [8.1394194e-04 2.7422693e-03 1.5687030e-04 2.1196797e-04 1.4467083e-03
 4.7671655e-03 1.8164331e-02 1.7818872e-02 1.5538953e-04 1.7800892e-04
 1.3744901e-03 1.7943252e-05 1.0063621e-03 1.7490137e-03 3.4545548e-03
 2.3102992e-04 4.8853375e-04 1.2276807e-03 3.1725955e-04 5.3413759e-04
 1.3176120e-02 1.7715689e-04 1.3434447e-04 1.8996557e-03 3.6607883e-03
 4.2502978e-03 6.3119180e-05 1.5023080e-02 3.9798398e-02 6.0887849e-03
 1.5662469e-04 1.6404817e-02 3.9129279e-04 1.6833516e-04 5.4639779e-02
 4.2017861e-04 2.0664912e-03 8.9486100e-04 2.0372382e-04 1.6111501e-04
 1.5664898e-02 1.4752984e-02 3.3800784e-03 1.4979863e-02 6.4210463e-01
 1.9515961e-02 1.6516501e-03 5.6746706e-02 1.3016198e-04 1.0647295e-04
 5.1385612e-04 1.1039268e-03 1.3012181e-05 1.8943982e-04 5.6069432e-04
 8.1670219e-03 1.1419101e-03 2.6413649e-03]
prediction length: 58
Before
[8.13941937e-04 2.74226931e-03 1.56870301e-04 2.11967970e-04
 1.44670834e-03 4.76716552e-03 1.81643311e-02 1.78188719e-02
 1.553895

58
prediction: [1.41703920e-03 1.75625889e-03 8.31700308e-05 2.15652399e-04
 9.70804715e-04 5.10471361e-03 3.56805734e-02 3.70201170e-02
 1.48023886e-04 2.88640847e-04 8.78648832e-04 4.06960316e-06
 5.92297176e-04 1.42509746e-03 2.54247175e-03 1.30471133e-04
 2.22893083e-04 1.41407805e-03 4.00043180e-04 3.35285877e-04
 1.64308660e-02 9.20548628e-05 7.03151309e-05 3.24474857e-03
 4.69011068e-03 3.06628877e-03 1.91050240e-05 1.78527534e-02
 7.75273293e-02 5.49756829e-03 2.01524541e-04 1.77358873e-02
 2.88713258e-04 2.40948910e-04 9.12831649e-02 4.22351353e-04
 1.49399636e-03 1.54228555e-03 1.03939645e-04 1.99022907e-04
 5.48639102e-03 7.10111670e-03 2.36863643e-03 1.47882244e-02
 5.58867395e-01 1.63490642e-02 2.35489593e-03 3.28213796e-02
 4.88293044e-05 5.59415494e-05 4.99892805e-04 2.91884970e-03
 9.41962298e-06 5.81490422e-05 6.08372444e-04 1.64997801e-02
 4.17318987e-03 2.35712598e-03]
prediction length: 58
Before
[1.41703920e-03 1.75625889e-03 8.31700308e-05 2.15652399e-04
 9.708047